In [1]:
%matplotlib inline


NLP From Scratch: Translation with a Sequence to Sequence Network and Attention
*******************************************************************************
**Author**: `Sean Robertson <https://github.com/spro/practical-pytorch>`_

This is the third and final tutorial on doing "NLP From Scratch", where we
write our own classes and functions to preprocess the data to do our NLP
modeling tasks. We hope after you complete this tutorial that you'll proceed to
learn how `torchtext` can handle much of this preprocessing for you in the
three tutorials immediately following this one.

In this project we will be teaching a neural network to translate from
French to English.

::

    [KEY: > input, = target, < output]

    > il est en train de peindre un tableau .
    = he is painting a picture .
    < he is painting a picture .

    > pourquoi ne pas essayer ce vin delicieux ?
    = why not try that delicious wine ?
    < why not try that delicious wine ?

    > elle n est pas poete mais romanciere .
    = she is not a poet but a novelist .
    < she not not a poet but a novelist .

    > vous etes trop maigre .
    = you re too skinny .
    < you re all alone .

... to varying degrees of success.

This is made possible by the simple but powerful idea of the `sequence
to sequence network <https://arxiv.org/abs/1409.3215>`__, in which two
recurrent neural networks work together to transform one sequence to
another. An encoder network condenses an input sequence into a vector,
and a decoder network unfolds that vector into a new sequence.

.. figure:: /_static/img/seq-seq-images/seq2seq.png
   :alt:

To improve upon this model we'll use an `attention
mechanism <https://arxiv.org/abs/1409.0473>`__, which lets the decoder
learn to focus over a specific range of the input sequence.

**Recommended Reading:**

I assume you have at least installed PyTorch, know Python, and
understand Tensors:

-  https://pytorch.org/ For installation instructions
-  :doc:`/beginner/deep_learning_60min_blitz` to get started with PyTorch in general
-  :doc:`/beginner/pytorch_with_examples` for a wide and deep overview
-  :doc:`/beginner/former_torchies_tutorial` if you are former Lua Torch user


It would also be useful to know about Sequence to Sequence networks and
how they work:

-  `Learning Phrase Representations using RNN Encoder-Decoder for
   Statistical Machine Translation <https://arxiv.org/abs/1406.1078>`__
-  `Sequence to Sequence Learning with Neural
   Networks <https://arxiv.org/abs/1409.3215>`__
-  `Neural Machine Translation by Jointly Learning to Align and
   Translate <https://arxiv.org/abs/1409.0473>`__
-  `A Neural Conversational Model <https://arxiv.org/abs/1506.05869>`__

You will also find the previous tutorials on
:doc:`/intermediate/char_rnn_classification_tutorial`
and :doc:`/intermediate/char_rnn_generation_tutorial`
helpful as those concepts are very similar to the Encoder and Decoder
models, respectively.

And for more, read the papers that introduced these topics:

-  `Learning Phrase Representations using RNN Encoder-Decoder for
   Statistical Machine Translation <https://arxiv.org/abs/1406.1078>`__
-  `Sequence to Sequence Learning with Neural
   Networks <https://arxiv.org/abs/1409.3215>`__
-  `Neural Machine Translation by Jointly Learning to Align and
   Translate <https://arxiv.org/abs/1409.0473>`__
-  `A Neural Conversational Model <https://arxiv.org/abs/1506.05869>`__


**Requirements**



In [2]:
from __future__ import unicode_literals, print_function, division
from io import open
import unicodedata
import string
import re
import random

import torch
import torch.nn as nn
from torch import optim
import torch.nn.functional as F

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

Loading data files
==================

The data for this project is a set of many thousands of English to
French translation pairs.

`This question on Open Data Stack
Exchange <https://opendata.stackexchange.com/questions/3888/dataset-of-sentences-translated-into-many-languages>`__
pointed me to the open translation site https://tatoeba.org/ which has
downloads available at https://tatoeba.org/eng/downloads - and better
yet, someone did the extra work of splitting language pairs into
individual text files here: https://www.manythings.org/anki/

The English to French pairs are too big to include in the repo, so
download to ``data/eng-fra.txt`` before continuing. The file is a tab
separated list of translation pairs:

::

    I am cold.    J'ai froid.

.. Note::
   Download the data from
   `here <https://download.pytorch.org/tutorial/data.zip>`_
   and extract it to the current directory.



Similar to the character encoding used in the character-level RNN
tutorials, we will be representing each word in a language as a one-hot
vector, or giant vector of zeros except for a single one (at the index
of the word). Compared to the dozens of characters that might exist in a
language, there are many many more words, so the encoding vector is much
larger. We will however cheat a bit and trim the data to only use a few
thousand words per language.

.. figure:: /_static/img/seq-seq-images/word-encoding.png
   :alt:





We'll need a unique index per word to use as the inputs and targets of
the networks later. To keep track of all this we will use a helper class
called ``Lang`` which has word → index (``word2index``) and index → word
(``index2word``) dictionaries, as well as a count of each word
``word2count`` to use to later replace rare words.




In [3]:
SOS_token = 0
EOS_token = 1


class Lang:
    def __init__(self, name):
        self.name = name
        self.word2index = {}
        self.word2count = {}
        self.index2word = {0: "SOS", 1: "EOS"}
        self.n_words = 2  # Count SOS and EOS

    def addSentence(self, sentence):
        for word in sentence.split(' '):
            self.addWord(word)

    def addWord(self, word):
        if word not in self.word2index:
            self.word2index[word] = self.n_words
            self.word2count[word] = 1
            self.index2word[self.n_words] = word
            self.n_words += 1
        else:
            self.word2count[word] += 1

The files are all in Unicode, to simplify we will turn Unicode
characters to ASCII, make everything lowercase, and trim most
punctuation.




In [4]:
# Turn a Unicode string to plain ASCII, thanks to
# https://stackoverflow.com/a/518232/2809427
def unicodeToAscii(s):
    return ''.join(
        c for c in unicodedata.normalize('NFD', s)
        if unicodedata.category(c) != 'Mn'
    )

# Lowercase, trim, and remove non-letter characters


def normalizeString(s):
    s = unicodeToAscii(s.lower().strip())
    s = re.sub(r"([.!?])", r" \1", s)
    s = re.sub(r"[^a-zA-Z.!?]+", r" ", s)
    return s

To read the data file we will split the file into lines, and then split
lines into pairs. The files are all English → Other Language, so if we
want to translate from Other Language → English I added the ``reverse``
flag to reverse the pairs.




In [5]:
def readLangs(lang1, lang2, reverse=False):
    print("Reading lines...")

    # Read the file and split into lines
    lines = open('data/%s-%s.txt' % (lang1, lang2), encoding='utf-8').\
        read().strip().split('\n')

    # Split every line into pairs and normalize
    pairs = [[normalizeString(s) for s in l.split('\t')] for l in lines]

    # Reverse pairs, make Lang instances
    if reverse:
        pairs = [list(reversed(p)) for p in pairs]
        input_lang = Lang(lang2)
        output_lang = Lang(lang1)
    else:
        input_lang = Lang(lang1)
        output_lang = Lang(lang2)

    return input_lang, output_lang, pairs

Since there are a *lot* of example sentences and we want to train
something quickly, we'll trim the data set to only relatively short and
simple sentences. Here the maximum length is 10 words (that includes
ending punctuation) and we're filtering to sentences that translate to
the form "I am" or "He is" etc. (accounting for apostrophes replaced
earlier).




In [6]:
MAX_LENGTH = 10

eng_prefixes = (
    "i am ", "i m ",
    "he is", "he s ",
    "she is", "she s ",
    "you are", "you re ",
    "we are", "we re ",
    "they are", "they re "
)


def filterPair(p):
    return len(p[0].split(' ')) < MAX_LENGTH and \
        len(p[1].split(' ')) < MAX_LENGTH and \
        p[1].startswith(eng_prefixes)


def filterPairs(pairs):
    return [pair for pair in pairs if filterPair(pair)]

The full process for preparing the data is:

-  Read text file and split into lines, split lines into pairs
-  Normalize text, filter by length and content
-  Make word lists from sentences in pairs




In [28]:
def prepareData(lang1, lang2, reverse=False):
    input_lang, output_lang, pairs = readLangs(lang1, lang2, reverse)
    print("Read %s sentence pairs" % len(pairs))
    pairs = filterPairs(pairs)
    print("Trimmed to %s sentence pairs" % len(pairs))
    print("Counting words...")
    for pair in pairs:
        input_lang.addSentence(pair[0])
        output_lang.addSentence(pair[1])
    print("Counted words:")
    print(input_lang.name, input_lang.n_words)
    print(output_lang.name, output_lang.n_words)
    return input_lang, output_lang, pairs


input_lang, output_lang, pairs = prepareData('eng', 'fra', True)
print(random.choice(pairs))

Reading lines...
Read 135842 sentence pairs
Trimmed to 10599 sentence pairs
Counting words...
Counted words:
fra 4345
eng 2803
['il est une autorite reconnue sur le sujet .', 'he is a recognized authority on the subject .']


The Seq2Seq Model
=================

A Recurrent Neural Network, or RNN, is a network that operates on a
sequence and uses its own output as input for subsequent steps.

A `Sequence to Sequence network <https://arxiv.org/abs/1409.3215>`__, or
seq2seq network, or `Encoder Decoder
network <https://arxiv.org/pdf/1406.1078v3.pdf>`__, is a model
consisting of two RNNs called the encoder and decoder. The encoder reads
an input sequence and outputs a single vector, and the decoder reads
that vector to produce an output sequence.

.. figure:: /_static/img/seq-seq-images/seq2seq.png
   :alt:

Unlike sequence prediction with a single RNN, where every input
corresponds to an output, the seq2seq model frees us from sequence
length and order, which makes it ideal for translation between two
languages.

Consider the sentence "Je ne suis pas le chat noir" → "I am not the
black cat". Most of the words in the input sentence have a direct
translation in the output sentence, but are in slightly different
orders, e.g. "chat noir" and "black cat". Because of the "ne/pas"
construction there is also one more word in the input sentence. It would
be difficult to produce a correct translation directly from the sequence
of input words.

With a seq2seq model the encoder creates a single vector which, in the
ideal case, encodes the "meaning" of the input sequence into a single
vector — a single point in some N dimensional space of sentences.




The Encoder
-----------

The encoder of a seq2seq network is a RNN that outputs some value for
every word from the input sentence. For every input word the encoder
outputs a vector and a hidden state, and uses the hidden state for the
next input word.

.. figure:: /_static/img/seq-seq-images/encoder-network.png
   :alt:





In [8]:
class EncoderRNN(nn.Module):
    def __init__(self, input_size, hidden_size):
        super(EncoderRNN, self).__init__()
        self.hidden_size = hidden_size

        self.embedding = nn.Embedding(input_size, hidden_size)
        self.gru = nn.GRU(hidden_size, hidden_size)

    def forward(self, input, hidden):
        embedded = self.embedding(input).view(1, 1, -1)
        output = embedded
        output, hidden = self.gru(output, hidden)
        return output, hidden

    def initHidden(self):
        return torch.zeros(1, 1, self.hidden_size, device=device)

The Decoder
-----------

The decoder is another RNN that takes the encoder output vector(s) and
outputs a sequence of words to create the translation.




Simple Decoder
^^^^^^^^^^^^^^

In the simplest seq2seq decoder we use only last output of the encoder.
This last output is sometimes called the *context vector* as it encodes
context from the entire sequence. This context vector is used as the
initial hidden state of the decoder.

At every step of decoding, the decoder is given an input token and
hidden state. The initial input token is the start-of-string ``<SOS>``
token, and the first hidden state is the context vector (the encoder's
last hidden state).

.. figure:: /_static/img/seq-seq-images/decoder-network.png
   :alt:





In [9]:
class DecoderRNN(nn.Module):
    def __init__(self, hidden_size, output_size):
        super(DecoderRNN, self).__init__()
        self.hidden_size = hidden_size

        self.embedding = nn.Embedding(output_size, hidden_size)
        self.gru = nn.GRU(hidden_size, hidden_size)
        self.out = nn.Linear(hidden_size, output_size)
        self.softmax = nn.LogSoftmax(dim=1)

    def forward(self, input, hidden):
        output = self.embedding(input).view(1, 1, -1)
        output = F.relu(output)
        output, hidden = self.gru(output, hidden)
        output = self.softmax(self.out(output[0]))
        return output, hidden

    def initHidden(self):
        return torch.zeros(1, 1, self.hidden_size, device=device)

I encourage you to train and observe the results of this model, but to
save space we'll be going straight for the gold and introducing the
Attention Mechanism.




Attention Decoder
^^^^^^^^^^^^^^^^^

If only the context vector is passed betweeen the encoder and decoder,
that single vector carries the burden of encoding the entire sentence.

Attention allows the decoder network to "focus" on a different part of
the encoder's outputs for every step of the decoder's own outputs. First
we calculate a set of *attention weights*. These will be multiplied by
the encoder output vectors to create a weighted combination. The result
(called ``attn_applied`` in the code) should contain information about
that specific part of the input sequence, and thus help the decoder
choose the right output words.

.. figure:: https://i.imgur.com/1152PYf.png
   :alt:

Calculating the attention weights is done with another feed-forward
layer ``attn``, using the decoder's input and hidden state as inputs.
Because there are sentences of all sizes in the training data, to
actually create and train this layer we have to choose a maximum
sentence length (input length, for encoder outputs) that it can apply
to. Sentences of the maximum length will use all the attention weights,
while shorter sentences will only use the first few.

.. figure:: /_static/img/seq-seq-images/attention-decoder-network.png
   :alt:





In [10]:
class AttnDecoderRNN(nn.Module):
    def __init__(self, hidden_size, output_size, dropout_p=0.1, max_length=MAX_LENGTH):
        super(AttnDecoderRNN, self).__init__()
        self.hidden_size = hidden_size
        self.output_size = output_size
        self.dropout_p = dropout_p
        self.max_length = max_length
        self.embedding = nn.Embedding(self.output_size, self.hidden_size)# hidden_size 256
        self.attn = nn.Linear(self.hidden_size * 2, self.max_length)
        self.attn_combine = nn.Linear(self.hidden_size * 2, self.hidden_size)
        self.dropout = nn.Dropout(self.dropout_p)
        self.gru = nn.GRU(self.hidden_size, self.hidden_size)
        self.out = nn.Linear(self.hidden_size, self.output_size)

    def forward(self, input, hidden, encoder_outputs):
        embedded = self.embedding(input).view(1, 1, -1)

        embedded = self.dropout(embedded)

        attn_weights = F.softmax(
            self.attn(torch.cat((embedded[0], hidden[0]), 1)), dim=1)
        attn_applied = torch.bmm(attn_weights.unsqueeze(0),
                                 encoder_outputs.unsqueeze(0))
        
        
        output = torch.cat((embedded[0], attn_applied[0]), 1)
        output = self.attn_combine(output).unsqueeze(0)

        output = F.relu(output)
        output, hidden = self.gru(output, hidden)

        output = F.log_softmax(self.out(output[0]), dim=1)
        return output, hidden, attn_weights

    def initHidden(self):
        return torch.zeros(1, 1, self.hidden_size, device=device)

<div class="alert alert-info"><h4>Note</h4><p>There are other forms of attention that work around the length
  limitation by using a relative position approach. Read about "local
  attention" in `Effective Approaches to Attention-based Neural Machine
  Translation <https://arxiv.org/abs/1508.04025>`__.</p></div>

Training
========

Preparing Training Data
-----------------------

To train, for each pair we will need an input tensor (indexes of the
words in the input sentence) and target tensor (indexes of the words in
the target sentence). While creating these vectors we will append the
EOS token to both sequences.




In [11]:
def indexesFromSentence(lang, sentence):
    return [lang.word2index[word] for word in sentence.split(' ')]


def tensorFromSentence(lang, sentence):
    indexes = indexesFromSentence(lang, sentence)
    indexes.append(EOS_token)
    return torch.tensor(indexes, dtype=torch.long, device=device).view(-1, 1)


def tensorsFromPair(pair):
    input_tensor = tensorFromSentence(input_lang, pair[0])
    target_tensor = tensorFromSentence(output_lang, pair[1])
    return (input_tensor, target_tensor)

Training the Model
------------------

To train we run the input sentence through the encoder, and keep track
of every output and the latest hidden state. Then the decoder is given
the ``<SOS>`` token as its first input, and the last hidden state of the
encoder as its first hidden state.

为了训练，我们通过编码器运行输入语句，并跟踪每个输出和最新的隐藏状态。然后，为解码器提供<SOS>令牌作为其第一个输入，并为编码器提供最后的隐藏状态作为其第一个隐藏状态。

"Teacher forcing" is the concept of using the real target outputs as
each next input, instead of using the decoder's guess as the next input.
Using teacher forcing causes it to converge faster but `when the trained
network is exploited, it may exhibit
instability <http://citeseerx.ist.psu.edu/viewdoc/download?doi=10.1.1.378.4095&rep=rep1&type=pdf>`__.

“教师强制”的概念是使用实际目标输出作为每个下一个输入，而不是使用解码器的猜测作为下一个输入。使用教师强迫会使其收敛更快，但是当利用受过训练的网络时，它可能会显示不稳定

You can observe outputs of teacher-forced networks that read with
coherent grammar but wander far from the correct translation -
intuitively it has learned to represent the output grammar and can "pick
up" the meaning once the teacher tells it the first few words, but it
has not properly learned how to create the sentence from the translation
in the first place.

您可以观察到以教师为主导的网络的输出，这些输出阅读的是连贯的语法，但却偏离了正确的翻译-直观地，它已经学会了代表输出语法，并且一旦老师讲了最初的几个单词就可以“理解”含义，但是 首先，它还没有正确地学习如何从翻译中创建句子。

Because of the freedom PyTorch's autograd gives us, we can randomly
choose to use teacher forcing or not with a simple if statement. Turn
``teacher_forcing_ratio`` up to use more of it.

由于PyTorch的autograd提供给我们的自由，我们可以随意
选择是否通过简单的if语句使用教师强制。 转
``teacher_forcing_ratio''最多使用它。


In [26]:
teacher_forcing_ratio = 0.5


def train(input_tensor, target_tensor, encoder, decoder, encoder_optimizer, decoder_optimizer, criterion, max_length=MAX_LENGTH):
    encoder_hidden = encoder.initHidden()

    encoder_optimizer.zero_grad()
    decoder_optimizer.zero_grad()

    input_length = input_tensor.size(0)
    target_length = target_tensor.size(0)

    encoder_outputs = torch.zeros(max_length, encoder.hidden_size, device=device)

    loss = 0

    for ei in range(input_length):
        encoder_output, encoder_hidden = encoder(
            input_tensor[ei], encoder_hidden)
        encoder_outputs[ei] = encoder_output[0, 0]

    decoder_input = torch.tensor([[SOS_token]], device=device)

    decoder_hidden = encoder_hidden
    
    use_teacher_forcing = True if random.random() < teacher_forcing_ratio else False

    if use_teacher_forcing:
        # Teacher forcing: Feed the target as the next input
        for di in range(target_length):
            decoder_output, decoder_hidden, decoder_attention = decoder(
                decoder_input, decoder_hidden, encoder_outputs)
            loss += criterion(decoder_output, target_tensor[di])
            decoder_input = target_tensor[di]  # Teacher forcing

    else:
        # Without teacher forcing: use its own predictions as the next input
        for di in range(target_length):
            decoder_output, decoder_hidden, decoder_attention = decoder(
                decoder_input, decoder_hidden, encoder_outputs)
            topv, topi = decoder_output.topk(1)
            decoder_input = topi.squeeze().detach()  # detach from history as input

            loss += criterion(decoder_output, target_tensor[di])
            if decoder_input.item() == EOS_token:
                break

    loss.backward()

    encoder_optimizer.step()
    decoder_optimizer.step()

    return loss.item() / target_length

This is a helper function to print time elapsed and estimated time
remaining given the current time and progress %.




In [13]:
import time
import math


def asMinutes(s):
    m = math.floor(s / 60)
    s -= m * 60
    return '%dm %ds' % (m, s)


def timeSince(since, percent):
    now = time.time()
    s = now - since
    es = s / (percent)
    rs = es - s
    return '%s (- %s)' % (asMinutes(s), asMinutes(rs))

The whole training process looks like this:

-  Start a timer
-  Initialize optimizers and criterion
-  Create set of training pairs
-  Start empty losses array for plotting

Then we call ``train`` many times and occasionally print the progress (%
of examples, time so far, estimated time) and average loss.




In [14]:
def trainIters(encoder, decoder, n_iters, print_every=1000, plot_every=100, learning_rate=0.01):
    start = time.time()
    plot_losses = []
    print_loss_total = 0  # Reset every print_every
    plot_loss_total = 0  # Reset every plot_every

    encoder_optimizer = optim.SGD(encoder.parameters(), lr=learning_rate)
    decoder_optimizer = optim.SGD(decoder.parameters(), lr=learning_rate)
    training_pairs = [tensorsFromPair(random.choice(pairs))
                      for i in range(n_iters)]
    criterion = nn.NLLLoss()

    for iter in range(1, n_iters + 1):
        training_pair = training_pairs[iter - 1]
        input_tensor = training_pair[0]
        target_tensor = training_pair[1]

        loss = train(input_tensor, target_tensor, encoder,
                     decoder, encoder_optimizer, decoder_optimizer, criterion)
        print_loss_total += loss
        plot_loss_total += loss

        if iter % print_every == 0:
            print_loss_avg = print_loss_total / print_every
            print_loss_total = 0
            print('%s (%d %d%%) %.4f' % (timeSince(start, iter / n_iters),
                                         iter, iter / n_iters * 100, print_loss_avg))

        if iter % plot_every == 0:
            plot_loss_avg = plot_loss_total / plot_every
            plot_losses.append(plot_loss_avg)
            plot_loss_total = 0

    showPlot(plot_losses)

Plotting results
----------------

Plotting is done with matplotlib, using the array of loss values
``plot_losses`` saved while training.




In [15]:
import matplotlib.pyplot as plt
plt.switch_backend('agg')
import matplotlib.ticker as ticker
import numpy as np


def showPlot(points):
    plt.figure()
    fig, ax = plt.subplots()
    # this locator puts ticks at regular intervals
    loc = ticker.MultipleLocator(base=0.2)
    ax.yaxis.set_major_locator(loc)
    plt.plot(points)

Evaluation
==========

Evaluation is mostly the same as training, but there are no targets so
we simply feed the decoder's predictions back to itself for each step.
Every time it predicts a word we add it to the output string, and if it
predicts the EOS token we stop there. We also store the decoder's
attention outputs for display later.




In [16]:
def evaluate(encoder, decoder, sentence, max_length=MAX_LENGTH):
    with torch.no_grad():
        input_tensor = tensorFromSentence(input_lang, sentence)
        input_length = input_tensor.size()[0]
        encoder_hidden = encoder.initHidden()

        encoder_outputs = torch.zeros(max_length, encoder.hidden_size, device=device)

        for ei in range(input_length):
            encoder_output, encoder_hidden = encoder(input_tensor[ei],
                                                     encoder_hidden)
            encoder_outputs[ei] += encoder_output[0, 0]

        decoder_input = torch.tensor([[SOS_token]], device=device)  # SOS

        decoder_hidden = encoder_hidden

        decoded_words = []
        decoder_attentions = torch.zeros(max_length, max_length)

        for di in range(max_length):
            decoder_output, decoder_hidden, decoder_attention = decoder(
                decoder_input, decoder_hidden, encoder_outputs)
            decoder_attentions[di] = decoder_attention.data
            topv, topi = decoder_output.data.topk(1)
            if topi.item() == EOS_token:
                decoded_words.append('<EOS>')
                break
            else:
                decoded_words.append(output_lang.index2word[topi.item()])

            decoder_input = topi.squeeze().detach()

        return decoded_words, decoder_attentions[:di + 1]

We can evaluate random sentences from the training set and print out the
input, target, and output to make some subjective quality judgements:




In [17]:
def evaluateRandomly(encoder, decoder, n=10):
    for i in range(n):
        pair = random.choice(pairs)
        print('>', pair[0])
        print('=', pair[1])
        output_words, attentions = evaluate(encoder, decoder, pair[0])
        output_sentence = ' '.join(output_words)
        print('<', output_sentence)
        print('')

Training and Evaluating
=======================

With all these helper functions in place (it looks like extra work, but
it makes it easier to run multiple experiments) we can actually
initialize a network and start training.

Remember that the input sentences were heavily filtered. For this small
dataset we can use relatively small networks of 256 hidden nodes and a
single GRU layer. After about 40 minutes on a MacBook CPU we'll get some
reasonable results.

.. Note::
   If you run this notebook you can train, interrupt the kernel,
   evaluate, and continue training later. Comment out the lines where the
   encoder and decoder are initialized and run ``trainIters`` again.




In [27]:
hidden_size = 256
encoder1 = EncoderRNN(input_lang.n_words, hidden_size).to(device)
attn_decoder1 = AttnDecoderRNN(hidden_size, output_lang.n_words, dropout_p=0.1).to(device)

# trainIters(encoder1, attn_decoder1, 75000, print_every=5000)
trainIters(encoder1, attn_decoder1, 10000, print_every=5000)

decode input and output:0,tensor([[0]], device='cuda:0'),tensor([[-7.9690, -7.8872, -8.0698,  ..., -7.8218, -7.7211, -7.9265]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:1,tensor([129], device='cuda:0'),tensor([[-7.9567, -7.8272, -7.9881,  ..., -7.8715, -7.8124, -7.8848]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:2,tensor([78], device='cuda:0'),tensor([[-7.9632, -7.8443, -7.8896,  ..., -7.8868, -7.8414, -7.9061]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:3,tensor([147], device='cuda:0'),tensor([[-7.9662, -7.8877, -7.9391,  ..., -7.8373, -7.9047, -7.9114]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:4,tensor([303], device='cuda:0'),tensor([[-7.8983, -7.8698, -7.8988,  ..., -7.9153, -7.8711, -7.9695]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:5,tensor([44], device='cuda:0'),tensor([[-7.9277, -7.9441, -8.0201,

decode input and output:3,tensor([147], device='cuda:0'),tensor([[-7.9512, -7.4023, -7.7894,  ..., -7.9186, -7.8905, -7.8853]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:4,tensor([98], device='cuda:0'),tensor([[-7.9202, -7.4172, -7.8370,  ..., -7.8738, -7.8688, -7.8321]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:5,tensor([158], device='cuda:0'),tensor([[-7.8916, -7.2982, -7.8164,  ..., -7.8956, -7.8642, -7.9151]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:6,tensor([155], device='cuda:0'),tensor([[-7.8350, -7.3187, -7.8052,  ..., -7.9629, -7.8687, -8.0013]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:7,tensor([4], device='cuda:0'),tensor([[-7.8028, -6.7075, -7.7475,  ..., -7.9674, -7.8761, -8.0305]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:0,tensor([[0]], device='cuda:0'),tensor([[-7.9182, -7.5967, -7.6166, 

decode input and output:0,tensor([[0]], device='cuda:0'),tensor([[-7.8387, -6.8930, -6.9506,  ..., -7.7489, -7.7103, -7.8593]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:1,tensor([129], device='cuda:0'),tensor([[-7.8506, -6.5483, -7.2253,  ..., -7.8186, -7.7990, -7.8756]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:2,tensor([124], device='cuda:0'),tensor([[-7.8282, -6.2179, -7.3065,  ..., -7.8259, -7.7707, -7.9601]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:3,tensor([33], device='cuda:0'),tensor([[-7.8654, -6.1036, -7.4623,  ..., -7.8899, -7.8757, -7.9942]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:4,tensor([532], device='cuda:0'),tensor([[-7.9224, -6.2170, -7.5537,  ..., -7.9181, -7.8199, -7.9863]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:5,tensor([1461], device='cuda:0'),tensor([[-7.8970, -6.2692, -7.461

decode input and output:0,tensor([[0]], device='cuda:0'),tensor([[-8.0053, -4.3295, -3.6932,  ..., -7.7342, -7.6692, -7.8824]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:1,tensor([2], device='cuda:0'),tensor([[-8.0315, -3.0156, -4.4879,  ..., -7.9690, -7.7541, -8.0099]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:2,tensor([3], device='cuda:0'),tensor([[-7.9872, -2.5408, -5.1930,  ..., -8.0346, -7.8492, -7.8505]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:3,tensor([170], device='cuda:0'),tensor([[-7.8731, -3.4286, -5.7470,  ..., -7.9115, -7.8308, -7.9080]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:4,tensor([4], device='cuda:0'),tensor([[-8.8140, -0.4280, -6.6620,  ..., -9.0823, -8.9155, -8.8952]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:0,tensor([[0]], device='cuda:0'),tensor([[-8.0344, -4.1226, -2.9666,  ..

decode input and output:0,tensor([[0]], device='cuda:0'),tensor([[-8.8960, -6.1482, -0.9355,  ..., -8.6121, -8.5025, -8.7987]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:1,tensor([14], device='cuda:0'),tensor([[-8.2592, -4.5780, -2.6178,  ..., -8.1954, -8.0615, -8.1905]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:2,tensor([40], device='cuda:0'),tensor([[-8.0375, -4.2937, -3.8588,  ..., -8.0884, -7.9873, -8.0768]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:3,tensor([147], device='cuda:0'),tensor([[-8.0646, -4.1833, -4.2414,  ..., -8.0349, -8.0433, -8.0704]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:4,tensor([504], device='cuda:0'),tensor([[-8.0162, -4.2793, -4.3598,  ..., -8.0817, -8.0251, -8.0812]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:5,tensor([102], device='cuda:0'),tensor([[-8.0022, -4.0783, -4.1964,

...

decode input and output:0,tensor([[0]], device='cuda:0'),tensor([[-1.6267e+01, -1.4317e+01, -1.2703e-03,  ..., -1.6009e+01,
         -1.6183e+01, -1.6032e+01]], device='cuda:0',
       grad_fn=<LogSoftmaxBackward>)
decode input and output:1,tensor([2], device='cuda:0'),tensor([[-14.7913, -14.1633, -10.8135,  ..., -14.6261, -14.0091, -14.0210]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:2,tensor([3], device='cuda:0'),tensor([[-13.3285, -13.9009, -15.4490,  ..., -13.6980, -13.5345, -12.6765]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:3,tensor([147], device='cuda:0'),tensor([[-10.6500,  -9.9781,  -6.6753,  ..., -10.5441, -10.9826, -10.0891]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:4,tensor([1613], device='cuda:0'),tensor([[-10.9866,  -6.9168,  -4.4329,  ..., -10.9015, -11.4001, -10.7026]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:5,tensor([69

decode input and output:0,tensor([[0]], device='cuda:0'),tensor([[-14.5775, -16.1535,  -4.5844,  ..., -14.4333, -14.6112, -14.4730]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:1,tensor([14], device='cuda:0'),tensor([[-13.6344, -14.9863, -11.6808,  ..., -13.9793, -13.6880, -13.6748]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:2,tensor([40], device='cuda:0'),tensor([[ -9.2891, -10.8328,  -9.7030,  ...,  -8.9867,  -9.6351,  -9.1009]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:3,tensor([1446], device='cuda:0'),tensor([[ -9.3267,  -7.9764,  -4.5674,  ...,  -9.1487, -10.1282,  -9.3419]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:4,tensor([1447], device='cuda:0'),tensor([[ -9.3667,  -5.8559,  -5.4768,  ...,  -9.4501, -10.1255,  -9.5704]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:5,tensor([4], device='cuda:0'),tenso

decode input and output:0,tensor([[0]], device='cuda:0'),tensor([[-15.2162, -16.0060,  -6.7979,  ..., -15.1939, -14.4257, -15.6245]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:1,tensor([129], device='cuda:0'),tensor([[-14.0913, -13.9561, -14.4727,  ..., -14.9471, -13.7706, -14.4674]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:2,tensor([78], device='cuda:0'),tensor([[-10.1058, -10.6414, -12.4358,  ..., -10.6091, -10.1470, -10.2202]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:3,tensor([151], device='cuda:0'),tensor([[-9.5170, -7.4372, -9.1819,  ..., -9.2174, -9.9780, -9.6613]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:4,tensor([2133], device='cuda:0'),tensor([[-10.6317,  -8.5383,  -7.2551,  ..., -10.8884, -11.1900, -11.0947]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:5,tensor([606], device='cuda:0'),tensor([[

decode input and output:4,tensor([4], device='cuda:0'),tensor([[-1.5330e+01, -5.2071e-03, -1.2313e+01,  ..., -1.5483e+01,
         -1.5252e+01, -1.5535e+01]], device='cuda:0',
       grad_fn=<LogSoftmaxBackward>)
decode input and output:0,tensor([[0]], device='cuda:0'),tensor([[-15.0312, -16.1500,  -6.2121,  ..., -14.8300, -15.0917, -15.0256]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:1,tensor([14], device='cuda:0'),tensor([[-13.9115, -15.9155, -12.8629,  ..., -14.1699, -14.1223, -14.1395]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:2,tensor([40], device='cuda:0'),tensor([[ -9.4971, -11.1907, -12.2480,  ...,  -9.0416,  -9.8557,  -9.1797]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:3,tensor([294], device='cuda:0'),tensor([[ -8.8908,  -7.0063, -10.4031,  ...,  -8.2871,  -9.5061,  -9.0135]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:4,tensor([655

decode input and output:5,tensor([1078], device='cuda:0'),tensor([[-11.0285,  -4.4523, -12.1767,  ..., -11.4658, -10.8872, -11.5075]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:6,tensor([4], device='cuda:0'),tensor([[-1.4352e+01, -1.2136e-02, -1.4654e+01,  ..., -1.4768e+01,
         -1.4479e+01, -1.4713e+01]], device='cuda:0',
       grad_fn=<LogSoftmaxBackward>)
decode input and output:0,tensor([[0]], device='cuda:0'),tensor([[-13.6951, -16.8726,  -5.2491,  ..., -13.6974, -13.4816, -13.7500]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:1,tensor([129], device='cuda:0'),tensor([[-12.3242, -12.8787, -13.3165,  ..., -12.8047, -12.0622, -12.2548]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:2,tensor([78], device='cuda:0'),tensor([[ -8.7454, -10.3940, -11.8504,  ...,  -9.4449,  -8.7714,  -8.8929]],
       device='cuda:0', grad_fn=<LogSoftmaxBackward>)
decode input and output:3,tensor([4

In [ ]:
evaluateRandomly(encoder1, attn_decoder1)

Visualizing Attention
---------------------

A useful property of the attention mechanism is its highly interpretable
outputs. Because it is used to weight specific encoder outputs of the
input sequence, we can imagine looking where the network is focused most
at each time step.

You could simply run ``plt.matshow(attentions)`` to see attention output
displayed as a matrix, with the columns being input steps and rows being
output steps:




In [ ]:
output_words, attentions = evaluate(
    encoder1, attn_decoder1, "je suis trop froid .")
plt.matshow(attentions.numpy())

For a better viewing experience we will do the extra work of adding axes
and labels:




In [ ]:
def showAttention(input_sentence, output_words, attentions):
    # Set up figure with colorbar
    fig = plt.figure()
    ax = fig.add_subplot(111)
    cax = ax.matshow(attentions.numpy(), cmap='bone')
    fig.colorbar(cax)

    # Set up axes
    ax.set_xticklabels([''] + input_sentence.split(' ') +
                       ['<EOS>'], rotation=90)
    ax.set_yticklabels([''] + output_words)

    # Show label at every tick
    ax.xaxis.set_major_locator(ticker.MultipleLocator(1))
    ax.yaxis.set_major_locator(ticker.MultipleLocator(1))

    plt.show()


def evaluateAndShowAttention(input_sentence):
    output_words, attentions = evaluate(
        encoder1, attn_decoder1, input_sentence)
    print('input =', input_sentence)
    print('output =', ' '.join(output_words))
    showAttention(input_sentence, output_words, attentions)


evaluateAndShowAttention("elle a cinq ans de moins que moi .")

evaluateAndShowAttention("elle est trop petit .")

evaluateAndShowAttention("je ne crains pas de mourir .")

evaluateAndShowAttention("c est un jeune directeur plein de talent .")

Exercises
=========

-  Try with a different dataset

   -  Another language pair
   -  Human → Machine (e.g. IOT commands)
   -  Chat → Response
   -  Question → Answer

-  Replace the embeddings with pre-trained word embeddings such as word2vec or
   GloVe
-  Try with more layers, more hidden units, and more sentences. Compare
   the training time and results.
-  If you use a translation file where pairs have two of the same phrase
   (``I am test \t I am test``), you can use this as an autoencoder. Try
   this:

   -  Train as an autoencoder
   -  Save only the Encoder network
   -  Train a new Decoder for translation from there


